In [1]:
#https://github.com/EmilStenstrom/conllu
#https://github.com/UniversalDependencies/UD_English-EWT
from conllu import parse, parse_tree
from collections import OrderedDict
import numpy as np

In [2]:
from enum import Enum
class Action_type(Enum):
    Left = 1
    Right = 2
    Reduse = 3
    Shift = 4
    
class oracle:
    def __init__(self, tree):
        self.rel=[]
        self.stack=[OrderedDict([('id', 0),('form','ROOT'),("head",0),("lemma","root")])]
        self.queue=tree
        self.step_processor={Action_type.Left:self.Left,
                             Action_type.Shift:self.Shift,
                             Action_type.Right:self.Right,
                             Action_type.Reduse:self.Reduse}
        
    def Shift(self):
        self.stack.append(self.queue.pop(0))
        
    def Left(self):
        self.rel.append((self.stack.pop()['id'],self.queue[0]['id']))
        
    def Right(self):
        self.rel.append((self.queue[0]['id'],self.stack[-1]['id']))
        self.stack.append(self.queue.pop(0))
        
    def Reduse(self):
        self.stack.pop()
        
    def do_steps(self, debug=False):
        history_step1=-1
        histiry_step2=-1
        self.features =[]
        self.labels = []
        self.dep = []
        while self.stack or self.queue:
            top_stack = self.stack[-1] if len(self.stack) > 0 else None
            first_queue =  self.queue[0] if len(self.queue) > 0 else None
            step_type=self.get_action(top_stack,first_queue)
            self.labels.append(step_type)
            if (step_type==Action_type.Left):
                self.dep.append(top_stack['deprel'])
            if (step_type==Action_type.Right):
                self.dep.append(first_queue['deprel'])
            else:
                self.dep.append('-')

            self.features.append(extract_features(self.stack, self.queue, self.rel,history_step1,histiry_step2))
            histiry_step2=history_step1
            history_step1=step_type.value
            if debug:
                self.info(step_type)
            self.step_processor[step_type]()
        return self.rel
    
    def get_action(self, stack,queue):
        if stack and not queue:
            return Action_type.Reduse
        if stack['head']==queue['id']:
             return Action_type.Left
        if stack['id']==queue['head']:
             return Action_type.Right
            
        if stack['id'] in  [i[0] for i in self.rel] and stack["id"] > queue["head"]:
             return Action_type.Reduse
        else:
            return Action_type.Shift
    
    def info(self, step_type):
        print('step: ', step_type)
        print('stack',  self.print_item(self.stack))
        print('queue',  self.print_item(self.queue))
        print('rel',  self.rel)
        print("====================================")

    def print_item(self, lst):
        return [i['form'] for i in lst]
    
    def get_relations(tree):
        return [(i['id'],i['head']) for i in tree]

In [3]:
# generate features
def extract_features(stack, queue, rel, history_step1, histiry_step2):
    #print("stack",stack)
    stack1=stack[-1]['lemma'] if len(stack)>0 else ''
    stack2=stack[-2]['lemma'] if len(stack)>1 else ''
    stack3=stack[-3]['lemma'] if len(stack)>2 else ''
    queue1=queue[0]['lemma'] if len(queue)>0 else ''
    queue2=queue[1]['lemma'] if len(queue)>1 else ''
    queue3=queue[2]['lemma'] if len(queue)>2 else ''
    queue4=queue[3]['lemma'] if len(queue)>4 else ''
    
    features = dict()
    if len(stack) > 0:
        stack_top = stack[-1]
        s0_features = get_pymorphy_word_features(stack_top["form"],'s0_',stack2,queue1, True  )
    else:
        s0_features = get_pymorphy_word_features('there_is_no_word','s0_',stack2,queue1 , True )
    features = {**features, **s0_features}
    
    if len(stack) > 1:
        s1_features = get_pymorphy_word_features(stack[-2]["form"],'s1_',stack2,queue1 , True )
    else:
        s1_features = get_pymorphy_word_features('there_is_no_word','s1_',stack2,queue1, True )
    features = {**features, **s1_features}
    
        
    if queue:
        queue_top = queue[0]
        q0_features = get_pymorphy_word_features(queue_top["form"],'q0_',stack1,queue2, True )
    else: 
        q0_features = get_pymorphy_word_features('there_is_no_word','q0_',stack1,queue2, True )
    features = {**features, **q0_features}
    
    if len(queue)>1:
        queue1 = queue[1]
        q1_features = get_pymorphy_word_features(queue1["form"],'q1_',stack1,queue3)
    else: 
        q1_features = get_pymorphy_word_features('there_is_no_word','q1_',stack1,queue3)
    features = {**features, **q1_features}
    
    if len(queue)>1:
        queue1 = queue[1]
        q2_features = get_pymorphy_word_features(queue1["form"],'q2_',stack1,queue4)
    else: 
        q2_features = get_pymorphy_word_features('there_is_no_word','q2_',stack1,queue4)
    features = {**features, **q2_features}
    
    features['history_step1']=history_step1
    features['histiry_step2']=histiry_step2


    features['stack_len']=len(stack)
    features['queue_len']=len(queue)
    features['rel_len']=len(rel)
    features['parrent_of']= sum([int(i[1]==stack_top['id']) for i in rel])
    if stack and queue:
        features["distance"] = queue[0]["id"] - stack[-1]["id"]
        features["word_index"] = queue[0]["id"]
    else:
        features["distance"]=-1
        features["word_index"]=-1
    return features

import pymorphy2
morph = pymorphy2.MorphAnalyzer(lang='uk')

def get_pymorphy_word_features(word, prefix, left, right, add_embeding=False):
    word_info = morph.parse(word)[0]
    try:
        left_tag = morph.parse(left)[0].tag.POS
    except:
        left_tag=''
    try:
        right_tag = morph.parse(right)[0].tag.POS
    except:
        right_tag=''

    features = dict()
    if add_embeding:
        try:
            features[prefix+'normal_form']=word_info.normal_form.lower()
        except:
            features[prefix+'normal_form']=''
            
    features[prefix+'POS']=str(word_info.tag.POS)
    features[prefix+'animacy']=str(word_info.tag.animacy)
    features[prefix+'aspect']=str(word_info.tag.aspect)
    features[prefix+'case']=str(word_info.tag.case)
    features[prefix+'number']=str(word_info.tag.number)
    features[prefix+'number']=str(word_info.tag.number)
    features[prefix+'person']=str(word_info.tag.person)
    features[prefix+'tense']=str(word_info.tag.tense)
    features[prefix+'transitivity']=str(word_info.tag.transitivity)
    features[prefix+'left_item']= '{0}_{1}'.format(left_tag, word_info.tag.POS)
    features[prefix+'item_right']= '{0}_{1}'.format(word_info.tag.POS,right_tag)
    features[prefix+'left_right']= '{0}_{1}'.format(left_tag, right_tag)

    return features

# collect  features

In [4]:
import pandas as pd

In [5]:
def get_vectors(trees):
    from tqdm import tqdm
    features =[]
    labels = []
    dep_labels = []


    for index in tqdm(range(0,len(trees))):
        tree=trees[index]
        o = oracle(tree.copy())
        parsed_relations = o.do_steps()
        features=features + o.features
        labels=labels + o.labels
        dep_labels=dep_labels+o.dep
    
    return features, labels, dep_labels

In [6]:
with open('../UD_Ukrainian-IU/uk_iu-ud-train.conllu') as f:
    c= f.read()
    trees= parse(c)

X_train, y_train, y_train_dep =get_vectors(trees)


100%|██████████| 4513/4513 [03:48<00:00, 19.78it/s]


In [7]:
from sklearn.feature_extraction import DictVectorizer
vectorizer = DictVectorizer(sparse=False)
X_train = vectorizer.fit_transform(X_train)

In [8]:
y_train = [i.value for i in y_train]

# get test

In [9]:
with open('../UD_Ukrainian-IU/uk_iu-ud-test.conllu') as f:
    c= f.read()
    trees= parse(c)

X_test, y_test, y_test_dep =get_vectors(trees)
X_test = vectorizer.transform(X_test)
y_test = [i.value for i in y_test] 

100%|██████████| 783/783 [00:40<00:00, 19.15it/s]


In [10]:
import gc
gc.collect()

503

In [11]:
trees

[[OrderedDict([('id', 1),
               ('form', 'Зречення'),
               ('lemma', 'зречення'),
               ('upostag', 'NOUN'),
               ('xpostag', 'Ncnsnn'),
               ('feats',
                OrderedDict([('Animacy', 'Inan'),
                             ('Case', 'Nom'),
                             ('Gender', 'Neut'),
                             ('Number', 'Sing')])),
               ('head', 6),
               ('deprel', 'nsubj'),
               ('deps', None),
               ('misc', OrderedDict([('Id', '01re')]))]),
  OrderedDict([('id', 2),
               ('form', 'культурної'),
               ('lemma', 'культурний'),
               ('upostag', 'ADJ'),
               ('xpostag', 'Afpfsgf'),
               ('feats',
                OrderedDict([('Case', 'Gen'),
                             ('Degree', 'Pos'),
                             ('Gender', 'Fem'),
                             ('Number', 'Sing')])),
               ('head', 3),
               ('deprel'

In [12]:
test_trees=trees

# build model

In [13]:
from sklearn.linear_model import SGDClassifier, LogisticRegression

In [14]:
clf = LogisticRegression( random_state=0)
clf.fit(X_train, y_train)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=0, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [15]:
predicted_test = clf.predict(X_test)

In [16]:
from sklearn.metrics import classification_report
print(classification_report(y_test, predicted_test, target_names=['Left','Right','Reduse','Shift']))

             precision    recall  f1-score   support

       Left       0.88      0.91      0.90      7352
      Right       0.78      0.79      0.79      7182
     Reduse       0.85      0.81      0.83      8370
      Shift       0.87      0.88      0.87      7757

avg / total       0.85      0.85      0.84     30661



# Calculate the unlabeled attachment score

In [17]:
def dep_parse(sentence, model):
    stack, queue, relations = [OrderedDict([('id', 0),('form','ROOT'),("head",0),("lemma","root")])], sentence[:], []
    history_step1=-1
    history_step2=-1
    while queue or stack:
        if stack and not queue:
            stack.pop()
        else:
            features = extract_features(stack, queue, relations,history_step1, history_step2)
            features = vectorizer.transform(features)
            action = model.predict(features)[0]
            # actual parsing
            if action == 4: #:Action_type.Shift:
                stack.append(queue.pop(0))
            elif action == 3: #:Action_type.Reduse:
                stack.pop()
            elif action == 1: #Action_type.Left:
                relations.append((stack[-1]["id"], queue[0]["id"]))
                stack.pop()
            elif action == 2: #Action_type.Right:
                relations.append((queue[0]["id"], stack[-1]["id"]))
                stack.append(queue.pop(0))
            else:
                print("Unknown action.", action)
            histiry_step2=history_step1
            history_step1=action
    return sorted(relations)

In [18]:
print([node["form"] for node in test_trees[1]])
print(dep_parse(test_trees[1], clf))
print([(node["id"], node["head"]) for node in test_trees[1]])

['Продавши', 'свій', 'шедевр', 'Меценатові', ',', 'еллінський', 'скульптор', 'споневажив', 'саме', 'мистецтво', ':', 'Ти', 'не', 'продався', ',', '—', 'гірше', '!']
[(1, 8), (2, 3), (3, 1), (4, 3), (5, 8), (6, 7), (7, 8), (8, 0), (9, 10), (10, 8), (11, 14), (12, 14), (13, 14), (14, 8), (15, 17), (16, 17), (17, 14), (18, 8)]
[(1, 8), (2, 3), (3, 1), (4, 1), (5, 1), (6, 7), (7, 8), (8, 0), (9, 10), (10, 8), (11, 14), (12, 14), (13, 14), (14, 8), (15, 17), (16, 17), (17, 14), (18, 14)]


# TEST on new sentenses

In [19]:
from nltk.tokenize import sent_tokenize, word_tokenize
def predict_pos(sentense):
    tokens = [{'form':word,'lemma':word,'id':index+1} for index, word in enumerate(word_tokenize(sentense))]
    deps = dep_parse(tokens, clf)
    for child_index, parent_index in deps:
        print("{0} <- {1}".format(tokens[child_index-1]['form'],  tokens[parent_index-1]['form'] if parent_index>0 else "ROOT" ))

In [20]:
sentenses = ['Перед довгими вихідними угорський лоукостер Wizz Air вирішив додати позитиву українським любителям подорожувати.',
             'Перебуваючи у гарному настрої виконавчий віце-президент і заступник генерального директора компанії Стівен Джонс не приховував, що має для України гарні новини.', 
             'Утім розкривати всі карти він не поспішав.',
             'Розпочати топ-менеджер вирішив з досягнень компанії та планів на майбутнє.',
             'Згодом розповів про нову розробку лоукостера та відповів на питання журналістів про те, як компанія планує вигравати конкуренцію у Ryanair, та чи збирається відновлювати діяльність української "дочки".']

In [21]:
predict_pos(sentenses[0])

Перед <- лоукостер
довгими <- лоукостер
вихідними <- лоукостер
угорський <- лоукостер
лоукостер <- ROOT
лоукостер <- вирішив
Wizz <- лоукостер
Air <- вирішив
вирішив <- ROOT
додати <- вирішив
позитиву <- додати
українським <- любителям
любителям <- додати
подорожувати <- додати
. <- вирішив


In [24]:
predict_pos(sentenses[1])

Перебуваючи <- заступник
у <- настрої
гарному <- настрої
настрої <- Перебуваючи
виконавчий <- віце-президент
віце-президент <- настрої
і <- заступник
заступник <- приховував
генерального <- директора
директора <- заступник
компанії <- директора
Стівен <- компанії
Джонс <- компанії
не <- приховував
приховував <- ROOT
, <- має
що <- має
має <- приховував
для <- України
України <- має
гарні <- новини
новини <- має
. <- приховував


In [25]:
predict_pos(sentenses[2])

Утім <- розкривати
розкривати <- ROOT
всі <- карти
карти <- розкривати
він <- поспішав
не <- поспішав
поспішав <- розкривати
. <- розкривати


In [26]:
predict_pos(sentenses[3])

Розпочати <- ROOT
топ-менеджер <- Розпочати
вирішив <- Розпочати
з <- досягнень
досягнень <- вирішив
компанії <- досягнень
та <- планів
планів <- компанії
на <- майбутнє
майбутнє <- досягнень
. <- Розпочати


In [27]:
predict_pos(sentenses[4])

Згодом <- розповів
розповів <- ROOT
про <- розробку
нову <- розробку
розробку <- розповів
лоукостера <- розробку
та <- відповів
відповів <- розповів
на <- питання
питання <- відповів
журналістів <- питання
про <- те
те <- питання
, <- планує
як <- планує
компанія <- планує
планує <- те
вигравати <- планує
конкуренцію <- вигравати
у <- Ryanair
Ryanair <- те
, <- збирається
та <- збирається
чи <- збирається
збирається <- те
відновлювати <- збирається
діяльність <- відновлювати
української <- дочки
дочки <- діяльність
'' <- збирається
. <- розповів


In [ ]:
Хочу сказати що ці результати мене дуже порадували оскільки більшість важливих звязків проставлені правильно.
І ще є насправді варіанти для покращення такі як:
    1 Використання динамічного оракула,
    2 Використання бильшого тренувального сету
    3 використання звязки w2v+word
    4 Постпросесинг
    5 Використовувати ймовірності 3-4 грам post тегів
